In [78]:
import pandas as pd

df = pd.read_parquet('df_encoded.parquet')
df

name                                        description  \
0     0.10 of a Second           Smart Indicators for Connected Vehicles    
1               12trix                        Math Lessons for Young Kids   
2      1E Therapeutics                          Novel RNA-targeting Drugs   
3           1MRobotics  Retail Automation Solutions with Nano Fulfillment   
4            1touch.io    Personal Data Flow Tracking and Data Cataloging   
...                ...                                                ...   
4981            YOW HR  Human Resources Engagement and Optimization Pl...   
4982   Yummi Home Food                      Marketplace for Homemade Food   
4983        Yung-Etgar               Custom Mechanized Harvesting Systems   
4984           YuviTal  Digital Health and Fitness Solutions for Organ...   
4985          Z-square  Microendoscope for Minimally Invasive Imaging ...   

        year         target    size        stage       raised  \
0     2019.0            B2B    1-10  Pre-Funding  Undisclosed   
1     2012.0       B2B, B2C    1-10  Pre-Funding  Undisclosed   
2     2021.0            B2B  51-200         Seed        $120M   
3     2021.0            B2B   11-50            A         $25M   
4     2017.0            B2B  51-200            A       $16.1M   
...      ...            ...     ...          ...          ...   
4981  2020.0     B2B, B2B2C    1-10  Pre-Funding  Undisclosed   
4982  2012.0            B2C   11-50  Pre-Funding  Undisclosed   
4983  1982.0            B2B  51-200       Mature  Undisclosed   
4984  2017.0  B2B, B2C, B2G   11-50  Pre-Funding  Undisclosed   
4985  2013.0            B2B   11-50         Seed         $10M   

                                                   tags  \
0     [connected-vehicles, adas, autonomous-vehicles...   
1     [sdg, schools, pre-k, serious-games, games, mo...   
2     [pharmaceuticals, chronic-disease, immunology,...   
3     [omni-channel, ecommerce, climate-tech, artifi...   
4     [enterprise-solutions, data-protection, cyber-...   
...                                                 ...   
4981  [content-creators, e-learning, software-applic...   
4982  [ecommerce, p2p, delivery, online-shopping, ma...   
4983  [crops, agtech, harvesting, machinery, sdg, cl...   
4984  [fitness, digital-wallet, discount, mobile-app...   
4985  [endoscopy, medical-devices, minimally-invasiv...   

                                           text_vector_  
0     [-0.031224824488162994, -0.06342269480228424, ...  
1     [-0.038649097084999084, 0.028091922402381897, ...  
2     [0.04561534896492958, -0.017776092514395714, 0...  
3     [0.0024080690927803516, -0.03042100928723812, ...  
4     [-0.01007091999053955, 0.10431888699531555, -0...  
...                                                 ...  
4981  [0.026961881667375565, 0.002459645736962557, -...  
4982  [0.0036857957020401955, 0.03582162782549858, -...  
4983  [0.027293115854263306, 0.010461761616170406, 0...  
4984  [0.02851911261677742, 0.05474231392145157, -0....  
4985  [0.012587728910148144, -0.07959864288568497, -...  

[4986 rows x 9 columns]

In [89]:
import os
os.system('pip install openpyxl')
os.system('pip install sentence-transformers')
import pandas as pd
import gradio as gr
from sentence_transformers import SentenceTransformer

model = SentenceTransformer('all-mpnet-base-v2') #all-MiniLM-L6-v2 #all-mpnet-base-v2

df = pd.read_parquet('df_encoded.parquet')
df['tags'] = df['tags'].apply(lambda x : str(x))
def parse_raised(x):
    if x == 'Undisclosed':
        return 0
    else: 
        quantifier = x[-1]
        x = float(x[1:-1])
        if quantifier == 'K':
            return x/1000
        elif quantifier == 'M':
            return x
df['raised'] = df['raised'].apply(lambda x : parse_raised(x))
df = df.reset_index(drop=True)

from sklearn.neighbors import NearestNeighbors
import numpy as np
import pandas as pd
from sentence_transformers import SentenceTransformer

In [92]:
def filter_df(df, column_name, filter_type, filter_value):
    if filter_type == '==':
        df_filtered = df[df[column_name]==filter_value]
    elif filter_type == '>=':
        df_filtered = df[df[column_name]>=filter_value]
    elif filter_type == '<=':
        df_filtered = df[df[column_name]<=filter_value]
    elif filter_type == 'contains':
        df_filtered = df[df['target'].str.contains(filter_value)]
    return df_filtered

def search(df, query):
    product = model.encode(query).tolist()
    # product = df.iloc[0]['text_vector_'] #use one of the products as sample

    #prepare model
    nbrs = NearestNeighbors(n_neighbors=20, algorithm='ball_tree').fit(df['text_vector_'].values.tolist())

    distances, indices = nbrs.kneighbors([product]) #input the vector of the reference object

    #print out the description of every recommended product
    return df.iloc[list(indices)[0]][['name', 'description', 'raised', 'year', 'target', 'size', 'stage', 'tags']]

#the first module becomes text1, the second module file1
def greet(size, target, raised, query): 
    df_size = filter_df(df, 'size', '==', size)
    df_target = filter_df(df_size, 'target', 'contains', target)
    def raised_zero(x):
        if x == 0:
            return 'Undisclosed'
        else:
            return x
    print('a')
    df_raised = df_target[(df_target['raised'] >= raised) | (df_target['raised'] == 0)]
    df_knn = search(df_raised, query)
    #we live the sorting for last
    df_knn = df_knn.sort_values('raised', ascending=False)
    df_knn['raised'] = df_knn['raised'].apply(lambda x : raised_zero(x))

    return df_knn

with gr.Blocks(theme=gr.themes.Soft(primary_hue='amber', secondary_hue='gray', neutral_hue='amber')) as demo:
    gr.Markdown(
    """
    # Gradio with History
    """
    )
    size = gr.Radio(['1-10', '11-50', '51-200', '201-500', '500+'], multiselect=False, value='11-50', label='size')
    target = gr.Radio(['B2B', 'B2C', 'B2G', 'B2B2C'], value='B2B', multiselect=False, label='target')
    raised = gr.Slider(0, 20, value=5, step_size=1, label="Minimum raising (in Millions)")
    query = gr.Textbox(label='Describe the Startup you are searching for', value='age reversing')
    btn = gr.Button(value="Search for a Startup")
    output1 = gr.DataFrame(label='value')
    # btn.click(greet, inputs='text', outputs=['dataframe'])
    btn.click(greet, [size, target, raised, query], [output1])
demo.launch(share=False)

c:\Users\ardit\AppData\Local\Programs\Python\Python39\lib\site-packages\gradio\deprecation.py:43: UserWarning: You have unused kwarg parameters in Radio, please remove them: {'multiselect': False}
  warnings.warn(
c:\Users\ardit\AppData\Local\Programs\Python\Python39\lib\site-packages\gradio\deprecation.py:43: UserWarning: You have unused kwarg parameters in Slider, please remove them: {'step_size': 1}
  warnings.warn(


Running on local URL:  http://127.0.0.1:7896

To create a public link, set `share=True` in `launch()`.


a
